# Incidence du syndrome grippal

In [8]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

Les données de l'incidence du syndrome grippal sont disponibles du site Web du [Réseau Sentinelles](http://www.sentiweb.fr/). Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à une semaine de la période demandée. Nous téléchargeons toujours le jeu de données complet, qui commence en 1984 et se termine avec une semaine récente.

Voici l'explication des colonnes données [sur le site d'origine](https://ns.sentiweb.fr/incidence/csv-schema-v1.json):

| Nom de colonne | Libellé de colonne                                                                                                                |
|----------------|-----------------------------------------------------------------------------------------------------------------------------------|
| week           | Semaine calendaire (ISO 8601)                                                                                                     |
| indicator      | Code de l'indicateur de surveillance                                                                                              |
| inc            | Estimation de l'incidence de consultations en nombre de cas                                                                       |
| inc_low        | Estimation de la borne inférieure de l'IC95% du nombre de cas de consultation                                                     |
| inc_up         | Estimation de la borne supérieure de l'IC95% du nombre de cas de consultation                                                     |
| inc100         | Estimation du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants)                                   |
| inc100_low     | Estimation de la borne inférieure de l'IC95% du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants) |
| inc100_up      | Estimation de la borne supérieure de l'IC95% du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants) |
| geo_insee      | Code de la zone géographique concernée (Code INSEE) http://www.insee.fr/fr/methodes/nomenclatures/cog/                            |
| geo_name       | Libellé de la zone géographique (ce libellé peut être modifié sans préavis)                                                       |

La première ligne du fichier CSV est un commentaire, que nous ignorons en précisant `skiprows=1`.

In [11]:
raw_data = pd.read_csv("incidence-PAY-3_15.06.2021.csv", skiprows=1)
raw_data
print(raw_data)

        week  indicator     inc   inc_low    inc_up  inc100  inc100_low  \
0     202122          3    7603    5204.0   10002.0      12         8.0   
1     202121          3    7841    5414.0   10268.0      12         8.0   
2     202120          3   10278    7540.0   13016.0      16        12.0   
3     202119          3    9539    6860.0   12218.0      14        10.0   
4     202118          3   12135    9165.0   15105.0      18        14.0   
5     202117          3   12058    8891.0   15225.0      18        13.0   
6     202116          3   16505   12735.0   20275.0      25        19.0   
7     202115          3   19306   15398.0   23214.0      29        23.0   
8     202114          3   21073   17099.0   25047.0      32        26.0   
9     202113          3   26413   22094.0   30732.0      40        33.0   
10    202112          3   30658   25919.0   35397.0      46        39.0   
11    202111          3   24988   20718.0   29258.0      38        32.0   
12    202110          3  

Y a-t-il des points manquants dans ce jeux de données ? Oui, la semaine 19 de l'année 1989 n'a pas de valeurs associées.

In [12]:
raw_data[raw_data.isnull().any(axis=1)]

week  indicator  inc  inc_low  inc_up  inc100  inc100_low  inc100_up  \
1673  198919          3    0      NaN     NaN       0         NaN        NaN   

     geo_insee geo_name  
1673        FR   France

Nous éliminons ce point, ce qui n'a pas d'impact fort sur notre analyse qui est assez simple.

In [13]:
data = raw_data.dropna().copy()
data

week  indicator     inc   inc_low    inc_up  inc100  inc100_low  \
0     202122          3    7603    5204.0   10002.0      12         8.0   
1     202121          3    7841    5414.0   10268.0      12         8.0   
2     202120          3   10278    7540.0   13016.0      16        12.0   
3     202119          3    9539    6860.0   12218.0      14        10.0   
4     202118          3   12135    9165.0   15105.0      18        14.0   
5     202117          3   12058    8891.0   15225.0      18        13.0   
6     202116          3   16505   12735.0   20275.0      25        19.0   
7     202115          3   19306   15398.0   23214.0      29        23.0   
8     202114          3   21073   17099.0   25047.0      32        26.0   
9     202113          3   26413   22094.0   30732.0      40        33.0   
10    202112          3   30658   25919.0   35397.0      46        39.0   
11    202111          3   24988   20718.0   29258.0      38        32.0   
12    202110          3   19539   15951.0   23127.0      30        25.0   
13    202109          3   17572   13926.0   21218.0      27        21.0   
14    202108          3   20882   16907.0   24857.0      32        26.0   
15    202107          3   22393   18303.0   26483.0      34        28.0   
16    202106          3   23183   19134.0   27232.0      35        29.0   
17    202105          3   22426   18445.0   26407.0      34        28.0   
18    202104          3   25804   21491.0   30117.0      39        32.0   
19    202103          3   21810   17894.0   25726.0      33        27.0   
20    202102          3   17320   13906.0   20734.0      26        21.0   
21    202101          3   21799   17778.0   25820.0      33        27.0   
22    202053          3   21220   16498.0   25942.0      32        25.0   
23    202052          3   16428   12285.0   20571.0      25        19.0   
24    202051          3   21619   17370.0   25868.0      33        27.0   
25    202050          3   16845   13220.0   20470.0      26        20.0   
26    202049          3   12939    9923.0   15955.0      20        15.0   
27    202048          3   13804   10641.0   16967.0      21        16.0   
28    202047          3   19085   15285.0   22885.0      29        23.0   
29    202046          3   24801   20503.0   29099.0      38        31.0   
...      ...        ...     ...       ...       ...     ...         ...   
1880  198521          3   26096   19621.0   32571.0      47        35.0   
1881  198520          3   27896   20885.0   34907.0      51        38.0   
1882  198519          3   43154   32821.0   53487.0      78        59.0   
1883  198518          3   40555   29935.0   51175.0      74        55.0   
1884  198517          3   34053   24366.0   43740.0      62        44.0   
1885  198516          3   50362   36451.0   64273.0      91        66.0   
1886  198515          3   63881   45538.0   82224.0     116        83.0   
1887  198514          3  134545  114400.0  154690.0     244       207.0   
1888  198513          3  197206  176080.0  218332.0     357       319.0   
1889  198512          3  245240  223304.0  267176.0     445       405.0   
1890  198511          3  276205  252399.0  300011.0     501       458.0   
1891  198510          3  353231  326279.0  380183.0     640       591.0   
1892  198509          3  369895  341109.0  398681.0     670       618.0   
1893  198508          3  389886  359529.0  420243.0     707       652.0   
1894  198507          3  471852  432599.0  511105.0     855       784.0   
1895  198506          3  565825  518011.0  613639.0    1026       939.0   
1896  198505          3  637302  592795.0  681809.0    1155      1074.0   
1897  198504          3  424937  390794.0  459080.0     770       708.0   
1898  198503          3  213901  174689.0  253113.0     388       317.0   
1899  198502          3   97586   80949.0  114223.0     177       147.0   
1900  198501          3   85489   65918.0  105060.0     155       120.0   
1901  198452          3   84830  

Nos données utilisent une convention inhabituelle: le numéro de
semaine est collé à l'année, donnant l'impression qu'il s'agit
de nombre entier. C'est comme ça que Pandas les interprète.
  
Un deuxième problème est que Pandas ne comprend pas les numéros de
semaine.  Il faut lui fournir les dates de début et de fin de
semaine. Nous utilisons pour cela la bibliothèque `isoweek`.

Comme la conversion des semaines est devenu assez complexe, nous
écrivons une petite fonction Python pour cela. Ensuite, nous
l'appliquons à tous les points de nos donnés. Les résultats vont
dans une nouvelle colonne 'period'.

In [ ]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

Il restent deux petites modifications à faire.

Premièrement, nous définissons les périodes d'observation
comme nouvel index de notre jeux de données. Ceci en fait
une suite chronologique, ce qui sera pratique par la suite.

Deuxièmement, nous trions les points par période, dans
le sens chronologique.

In [ ]:
sorted_data = data.set_index('period').sort_index()

Nous vérifions la cohérence des données. Entre la fin d'une période et
le début de la période qui suit, la différence temporelle doit être
zéro, ou au moins très faible. Nous laissons une "marge d'erreur"
d'une seconde.

Ceci s'avère tout à fait juste sauf pour deux périodes consécutives
entre lesquelles il manque une semaine.

Nous reconnaissons ces dates: c'est la semaine sans observations
que nous avions supprimées !

In [ ]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

Un premier regard sur les données !

In [ ]:
sorted_data['inc'].plot()

Un zoom sur les dernières années montre mieux la situation des pics en hiver. Le creux des incidences se trouve en été.

In [ ]:
sorted_data['inc'][-200:].plot()

## Etude de l'incidence annuelle

Etant donné que le pic de l'épidémie se situe en hiver, à cheval
entre deux années civiles, nous définissons la période de référence
entre deux minima de l'incidence, du 1er août de l'année $N$ au
1er août de l'année $N+1$.

Notre tâche est un peu compliquée par le fait que l'année ne comporte
pas un nombre entier de semaines. Nous modifions donc un peu nos périodes
de référence: à la place du 1er août de chaque année, nous utilisons le
premier jour de la semaine qui contient le 1er août.

Comme l'incidence de syndrome grippal est très faible en été, cette
modification ne risque pas de fausser nos conclusions.

Encore un petit détail: les données commencent an octobre 1984, ce qui
rend la première année incomplète. Nous commençons donc l'analyse en 1985.

In [ ]:
first_august_week = [pd.Period(pd.Timestamp(y, 8, 1), 'W')
                     for y in range(1985,
                                    sorted_data.index[-1].year)]

En partant de cette liste des semaines qui contiennent un 1er août, nous obtenons nos intervalles d'environ un an comme les périodes entre deux semaines adjacentes dans cette liste. Nous calculons les sommes des incidences hebdomadaires pour toutes ces périodes.

Nous vérifions également que ces périodes contiennent entre 51 et 52 semaines, pour nous protéger contre des éventuelles erreurs dans notre code.

In [ ]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_august_week[:-1],
                        first_august_week[1:]):
    one_year = sorted_data['inc'][week1:week2-1]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)
yearly_incidence = pd.Series(data=yearly_incidence, index=year)

Voici les incidences annuelles.

In [ ]:
yearly_incidence.plot(style='*')

Une liste triée permet de plus facilement répérer les valeurs les plus élevées (à la fin).

In [ ]:
yearly_incidence.sort_values()

Enfin, un histogramme montre bien que les épidémies fortes, qui touchent environ 10% de la population
  française, sont assez rares: il y en eu trois au cours des 35 dernières années.

In [ ]:
yearly_incidence.hist(xrot=20)